In [28]:
import pandas as pd

In [29]:
url = 'http://www.ipeadata.gov.br/ExibeSerie.aspx?module=m&serid=1650971490&oper=view'

dados = pd.read_html(url, attrs={'id': 'grd_DXMainTable'})[0]  # Substitua 'ID_DA_TABELA' pelo ID real da tabela

dados = dados[1:]

In [30]:
dados.columns = ['data', 'preco']
dados['data'] = pd.to_datetime(dados['data'], format='%d/%m/%Y')
dados['preco'] = (dados['preco'].astype(int) / 100).round(2).astype(float)
dados = dados.sort_values(by='data')
dados.to_csv('historico_preco_barril_petroleo.csv', index=False)
dados = dados.set_index('data')
dados = dados.asfreq('D').ffill()
dados

preco
data             
1987-05-20  18.63
1987-05-21  18.45
1987-05-22  18.55
1987-05-23  18.55
1987-05-24  18.55
...           ...
2024-11-14  73.39
2024-11-15  73.45
2024-11-16  73.45
2024-11-17  73.45
2024-11-18  74.35

[13698 rows x 1 columns]

In [31]:
dados_prophet = dados.copy()
dados_prophet.reset_index(inplace=True)
# Renomeando as colunas
dados_prophet.rename(columns={'data': 'ds', 'preco': 'y'}, inplace = True)
dados_prophet

ds      y
0     1987-05-20  18.63
1     1987-05-21  18.45
2     1987-05-22  18.55
3     1987-05-23  18.55
4     1987-05-24  18.55
...          ...    ...
13693 2024-11-14  73.39
13694 2024-11-15  73.45
13695 2024-11-16  73.45
13696 2024-11-17  73.45
13697 2024-11-18  74.35

[13698 rows x 2 columns]

In [32]:
import plotly.express as px

fig = px.line(dados_prophet, x='ds', y='y')
fig.show()

In [33]:
from prophet import Prophet

In [34]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet()

# Treinar o modelo
modelo.fit(dados_prophet)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/559gmrn2.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/ugfad66_.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=85905', 'data', 'file=/tmp/tmp9oiqv76u/559gmrn2.json', 'init=/tmp/tmp9oiqv76u/ugfad66_.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_model6go_vmkk/prophet_model-20241124185319.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
18:53:19 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
18:53:26 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [35]:
previsao['ds'].max()

Timestamp('2025-11-18 00:00:00')

In [36]:
from prophet.plot import plot_plotly
fig = plot_plotly(modelo, previsao)
# Define os limites para o eixo x (substitua 'YYYY-MM-DD' pelas datas desejadas)
fig.update_layout(xaxis=dict(range=[previsao['ds'].min(), previsao['ds'].max()]))
fig.show()

In [37]:
previsao[['ds', 'yhat', 'yhat_lower', 'yhat_upper']]

ds       yhat  yhat_lower  yhat_upper
0     1987-05-20  16.788892    2.774813   30.332508
1     1987-05-21  16.875274    2.320636   30.285622
2     1987-05-22  16.910738    4.274225   29.978813
3     1987-05-23  16.903559    3.694176   31.826576
4     1987-05-24  16.932321    1.928930   30.847240
...          ...        ...         ...         ...
14058 2025-11-14  93.133937   78.855259  106.706427
14059 2025-11-15  93.076729   77.700529  107.337824
14060 2025-11-16  93.059217   77.790757  108.416483
14061 2025-11-17  93.074794   77.630095  108.109541
14062 2025-11-18  93.022033   78.725902  107.762883

[14063 rows x 4 columns]

In [38]:
from prophet.plot import plot_components_plotly

plot_components_plotly(modelo, previsao)

/usr/local/lib/python3.10/dist-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



In [39]:
dados.shape

(13698, 1)

In [40]:
treino = dados_prophet.iloc[:-365]
teste = dados_prophet.iloc[-365:]

In [41]:
treino.tail()

ds      y
13328 2023-11-15  82.40
13329 2023-11-16  77.73
13330 2023-11-17  81.22
13331 2023-11-18  81.22
13332 2023-11-19  81.22

In [42]:
teste.head()

ds      y
13333 2023-11-20  83.25
13334 2023-11-21  82.42
13335 2023-11-22  81.76
13336 2023-11-23  80.85
13337 2023-11-24  79.82

In [43]:
teste.tail()

ds      y
13693 2024-11-14  73.39
13694 2024-11-15  73.45
13695 2024-11-16  73.45
13696 2024-11-17  73.45
13697 2024-11-18  74.35

In [44]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet()

# Treinar o modelo
modelo.fit(treino)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/250bcmcx.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/lds2fxwi.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=84804', 'data', 'file=/tmp/tmp9oiqv76u/250bcmcx.json', 'init=/tmp/tmp9oiqv76u/lds2fxwi.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_modelr79wzok4/prophet_model-20241124185349.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
18:53:49 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
18:54:00 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [45]:
previsao.tail()

ds      trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
13693 2024-11-14  94.799979   79.970476  107.839620    89.163007    99.353357   
13694 2024-11-15  94.816162   78.558001  109.463910    89.145242    99.376949   
13695 2024-11-16  94.832345   78.977555  107.939124    89.129219    99.400379   
13696 2024-11-17  94.848528   79.837115  107.992520    89.104150    99.427876   
13697 2024-11-18  94.864711   77.654944  107.112266    89.071191    99.466488   

       additive_terms  additive_terms_lower  additive_terms_upper    weekly  \
13693       -1.134715             -1.134715             -1.134715  0.007368   
13694       -1.176461             -1.176461             -1.176461  0.017958   
13695       -1.261716             -1.261716             -1.261716 -0.015947   
13696       -1.307011             -1.307011             -1.307011 -0.010503   
13697       -1.310075             -1.310075             -1.310075  0.036924   

       weekly_lower  weekly_upper    yearly  yearly_lower  yearly_upper  \
13693      0.007368      0.007368 -1.142084     -1.142084     -1.142084   
13694      0.017958      0.017958 -1.194418     -1.194418     -1.194418   
13695     -0.015947     -0.015947 -1.245769     -1.245769     -1.245769   
13696     -0.010503     -0.010503 -1.296508     -1.296508     -1.296508   
13697      0.036924      0.036924 -1.346999     -1.346999     -1.346999   

       multiplicative_terms  multiplicative_terms_lower  \
13693                   0.0                         0.0   
13694                   0.0                         0.0   
13695                   0.0                         0.0   
13696                   0.0                         0.0   
13697                   0.0                         0.0   

       multiplicative_terms_upper       yhat  
13693                         0.0  93.665264  
13694                         0.0  93.639701  
13695                         0.0  93.570629  
13696                         0.0  93.541516  
13697                         0.0  93.554635

In [46]:
teste.tail()

ds      y
13693 2024-11-14  73.39
13694 2024-11-15  73.45
13695 2024-11-16  73.45
13696 2024-11-17  73.45
13697 2024-11-18  74.35

In [47]:
import plotly.graph_objects as go

fig = plot_plotly(modelo, previsao)
# Adicionar a nova série ao gráfico
fig.add_trace(
    go.Scatter(
        x=teste['ds'],  # Eixo x: datas
        y=teste['y'],   # Eixo y: valores
        mode='lines',        # Estilo da linha
        name='Teste',   # Nome da legenda
        line=dict(color='red')  # Cor da linha
    )
)
# Define os limites para o eixo x (substitua 'YYYY-MM-DD' pelas datas desejadas)
fig.update_layout(xaxis=dict(range=[previsao['ds'].min(), previsao['ds'].max()]))
fig.show()

In [48]:
# Juntando previsões com o conjunto de teste para comparação
dados_previsao = previsao[['ds', 'yhat']]
dados_comparacao = pd.merge(dados_previsao, teste, on='ds', how='inner')
dados_comparacao

ds       yhat      y
0   2023-11-20  87.600786  83.25
1   2023-11-21  87.529355  82.42
2   2023-11-22  87.456890  81.76
3   2023-11-23  87.463810  80.85
4   2023-11-24  87.436534  79.82
..         ...        ...    ...
360 2024-11-14  93.665264  73.39
361 2024-11-15  93.639701  73.45
362 2024-11-16  93.570629  73.45
363 2024-11-17  93.541516  73.45
364 2024-11-18  93.554635  74.35

[365 rows x 3 columns]

A métrica MSE *(Mean Squared Error)* é uma medida comum de avaliação de desempenho para modelos de regressão e previsão. Ela calcula a média dos quadrados das diferenças entre os valores previstos pelo modelo e os valores reais observados nos dados de teste. Matematicamente, o MSE é calculado pela fórmula:

$MSE = \frac{\sum_{} (y_i - \hat{y}_i)^2}{n}$

No entanto, o MSE tem uma limitação: suas unidades são quadráticas em relação às unidades originais dos dados. Isso pode tornar difícil interpretar o seu valor
Para superar essa limitação, muitas vezes é preferível usar o RMSE *(Root Mean Squared Error)*. O RMSE é simplesmente a raiz quadrada do MSE e é calculado pela fórmula:

$RMSE = \sqrt{MSE}$


In [49]:
from sklearn.metrics import mean_squared_error

# Calculando métricas de erro
mse = mean_squared_error(dados_comparacao['y'], dados_comparacao['yhat']).round(2)
rmse = np.sqrt(mse).round(2)

print(f'MSE: {mse}, RMSE: {rmse}')

MSE: 155.83, RMSE: 12.48


changepoint_prior_scale: é um dos mais importantes no modelo Prophet, pois determina a flexibilidade da tendência. Especificamente, ele controla o quanto a tendência pode mudar nos pontos de mudança (changepoints). Se o valor deste parâmetro for muito pequeno, a tendência será pouco ajustada (underfit), e variações que deveriam ser modeladas como mudanças na tendência acabarão sendo tratadas como ruído. Por outro lado, se o valor for muito grande, a tendência será excessivamente ajustada (overfit), podendo até capturar sazonalidades anuais, o que não é desejado. O valor padrão de 0.05 funciona bem para muitas séries temporais, mas pode ser ajustado. Uma faixa de valores recomendada é entre 0.001 e 0.5, geralmente ajustados em uma escala logarítmica.

In [50]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet(changepoint_prior_scale=0.5)

# Treinar o modelo
modelo.fit(treino)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

# Juntando previsões com o conjunto de teste para comparação
dados_previsao = previsao[['ds', 'yhat']]
dados_comparacao = pd.merge(dados_previsao, teste, on='ds', how='inner')

# Calculando métricas de erro
mse = mean_squared_error(dados_comparacao['y'], dados_comparacao['yhat']).round(2)
rmse = np.sqrt(mse).round(2)

print(f'MSE: {mse}, RMSE: {rmse}')

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/iilc4gzx.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/lftx5s0k.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=91537', 'data', 'file=/tmp/tmp9oiqv76u/iilc4gzx.json', 'init=/tmp/tmp9oiqv76u/lftx5s0k.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_model5e9nilpi/prophet_model-20241124185420.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
18:54:20 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
18:54:29 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


MSE: 149.01, RMSE: 12.21


changepoint_range: define a proporção do histórico onde os pontos de mudança de tendência serão estimados. O valor padrão é 0.8, ou seja, 80% do histórico, significando que o modelo não ajustará mudanças de tendência nos últimos 20% da série temporal. Isso é feito para evitar sobreajuste nas mudanças de tendência no final da série, onde pode não haver dados suficientes para um bom ajuste. Em contextos totalmente automatizados, pode ser benéfico ser menos conservador com esse parâmetro. Em um grande número de séries temporais, uma faixa razoável para este parâmetro seria entre 0.8 e 0.95.

In [51]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet(changepoint_prior_scale=0.5,
                 changepoint_range=0.95)

# Treinar o modelo
modelo.fit(treino)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

# Juntando previsões com o conjunto de teste para comparação
dados_previsao = previsao[['ds', 'yhat']]
dados_comparacao = pd.merge(dados_previsao, teste, on='ds', how='inner')

# Calculando métricas de erro
mse = mean_squared_error(dados_comparacao['y'], dados_comparacao['yhat']).round(2)
rmse = np.sqrt(mse).round(2)

print(f'MSE: {mse}, RMSE: {rmse}')

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/iio7bdzf.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/o_h8jkni.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=35117', 'data', 'file=/tmp/tmp9oiqv76u/iio7bdzf.json', 'init=/tmp/tmp9oiqv76u/o_h8jkni.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_model9sjeabli/prophet_model-20241124185437.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
18:54:37 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
18:54:47 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


MSE: 59.05, RMSE: 7.68


yearly_seasonality

A sazonalidade representa padrões periódicos que ocorrem em intervalos regulares, como efeitos semanais, mensais ou anuais. Para modelar e prever esse efeito, o Prophet utiliza séries de Fourier.

De modo prático, o ideal é aplicar essa mudança (N=20) quando estamos lidando com séries que apresentam padrões sazonais complexos, que precisam se ajustar a mudanças de frequência mais alta e geralmente são menos suaves. Se os dados não apresentarem flutuações sazonais de alta frequência, manter N = 10 é suficiente.

In [52]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet(changepoint_prior_scale=0.5,
                 changepoint_range=0.95,
                  yearly_seasonality=20)

# Treinar o modelo
modelo.fit(treino)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

# Juntando previsões com o conjunto de teste para comparação
dados_previsao = previsao[['ds', 'yhat']]
dados_comparacao = pd.merge(dados_previsao, teste, on='ds', how='inner')

# Calculando métricas de erro
mse = mean_squared_error(dados_comparacao['y'], dados_comparacao['yhat']).round(2)
rmse = np.sqrt(mse).round(2)

print(f'MSE: {mse}, RMSE: {rmse}')

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/w_hrzswz.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/lt95zg5q.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=35727', 'data', 'file=/tmp/tmp9oiqv76u/w_hrzswz.json', 'init=/tmp/tmp9oiqv76u/lt95zg5q.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_modelijnv2zrv/prophet_model-20241124185454.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
18:54:54 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
18:55:12 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


MSE: 57.3, RMSE: 7.57


In [54]:
# Criando o DataFrame de eventos de crise
crises = pd.DataFrame({
    'holiday': ['crise_financeira', 'colapso_petroleo', 'pandemia_covid', 'guerra_ucrania'],
    'ds': ['2008-06-01', '2014-06-01', '2020-02-01', '2022-02-01'],
    'lower_window': [0, 0, 0, 0],
    'upper_window': [240, 600, 210, 150]  # Duração do impacto da crise em dias
})

In [57]:
# Definir um seed
import numpy as np
np.random.seed(666)

# Instanciar o modelo Prophet
modelo = Prophet(changepoint_prior_scale=0.5,
                 changepoint_range=0.95,
                  yearly_seasonality=20,
                holidays=crises)

# Treinar o modelo
modelo.fit(treino)

# Criar um dataframe para previsões futuras
futuro = modelo.make_future_dataframe(periods=365, freq='D')
previsao = modelo.predict(futuro)

# Juntando previsões com o conjunto de teste para comparação
dados_previsao = previsao[['ds', 'yhat']]
dados_comparacao = pd.merge(dados_previsao, teste, on='ds', how='inner')

# Calculando métricas de erro
mse = mean_squared_error(dados_comparacao['y'], dados_comparacao['yhat']).round(2)
rmse = np.sqrt(mse).round(2)

print(f'MSE: {mse}, RMSE: {rmse}')

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/8pnm07fn.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/suan5ip6.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=99120', 'data', 'file=/tmp/tmp9oiqv76u/8pnm07fn.json', 'init=/tmp/tmp9oiqv76u/suan5ip6.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_modelhyd1222j/prophet_model-20241124190028.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
19:00:28 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
19:05:51 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


MSE: 23.73, RMSE: 4.87


In [58]:
import plotly.graph_objects as go

fig = plot_plotly(modelo, previsao)
# Adicionar a nova série ao gráfico
fig.add_trace(
    go.Scatter(
        x=teste['ds'],  # Eixo x: datas
        y=teste['y'],   # Eixo y: valores
        mode='lines',        # Estilo da linha
        name='Teste',   # Nome da legenda
        line=dict(color='red')  # Cor da linha
    )
)
# Define os limites para o eixo x (substitua 'YYYY-MM-DD' pelas datas desejadas)
fig.update_layout(xaxis=dict(range=[previsao['ds'].min(), previsao['ds'].max()]))
fig.show()

In [59]:
# Instanciar o modelo Prophet
modelo_final = Prophet(changepoint_prior_scale=0.5,
                 changepoint_range=0.95,
                  yearly_seasonality=20,
                  holidays=crises)

# Treinar o modelo
modelo_final.fit(dados_prophet)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/mzap2401.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmp9oiqv76u/upxcdqgi.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.10/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=77141', 'data', 'file=/tmp/tmp9oiqv76u/mzap2401.json', 'init=/tmp/tmp9oiqv76u/upxcdqgi.json', 'output', 'file=/tmp/tmp9oiqv76u/prophet_model7j74mmm3/prophet_model-20241124190827.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
19:08:27 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
19:12:20 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [60]:
import json

In [61]:
from prophet.serialize import model_to_json

In [62]:
with open('modelo_prophet.json', 'w') as file_out:
    json.dump(model_to_json(modelo_final), file_out)